# Domain generation

In [1]:
import time

from eminus import Atoms, read_xyz, SCF
from eminus.domains import domain_cuboid, domain_isovalue, domain_sphere, truncate
from eminus.energies import get_Esic, get_n_single
from eminus.extras import view_atoms

In [2]:
# Start by creating an `Atoms` object for lithium hydride
# Use a small `s` to make the resulting grid not too dense to display it
atoms = Atoms(*read_xyz('LiH.xyz'), ecut=3, center=True, Nspin=1)
scf = SCF(atoms)
scf.run();

XYZ file comment: "Experimental geometry from CCCBDB: https://cccbdb.nist.gov/exp2x.asp?casno=7580678&charge=0"
Start auto minimization...
Method  Iteration  Etot [Eh]    ΔEtot [Eh]   |Gradient|   
pccg           1   +2.798999    
sd             2   +2.111312    +6.8769e-01  [+4.08e+03]  
pccg           3   -2.192084    +4.3034e+00  [+3.62e+03]  
pccg           4   -4.043878    +1.8518e+00  [+2.87e+02]  
pccg           5   -4.720003    +6.7613e-01  [+3.60e+01]  
pccg           6   -4.854304    +1.3430e-01  [+5.65e+00]  
pccg           7   -4.893142    +3.8838e-02  [+1.19e+00]  
pccg           8   -4.905050    +1.1908e-02  [+3.01e-01]  
pccg           9   -4.910030    +4.9799e-03  [+1.14e-01]  
pccg          10   -4.912097    +2.0672e-03  [+6.23e-02]  
pccg          11   -4.912767    +6.7014e-04  [+2.00e-02]  
pccg          12   -4.912988    +2.2104e-04  [+7.16e-03]  
pccg          13   -4.913027    +3.8929e-05  [+1.48e-03]  
pccg          14   -4.913036    +8.7157e-06  [+3.01e-04]  
pc

In [3]:
# Create a boolean mask for a cuboidal domain
# This will create a domain with side lengths of 3 Bohr,
# with the center in the center at the center of mass of our molecule
mask = domain_cuboid(atoms, 3)

# Display the domain along with the atom positions
# The `view_atoms` function can be used outside of notebooks
view_atoms(atoms, atoms.r[mask])

In [4]:
# The same can be done for a spherical domain with a radius of 3 Bohr
mask = domain_sphere(atoms, 3)
view_atoms(atoms, atoms.r[mask])

In [5]:
# One can also define more than one center
# This will create multiple domains and merge them, here shown with the atom positions as centers
mask = domain_sphere(atoms, 3, atoms.X)
view_atoms(atoms, atoms.r[mask])

In [6]:
# An isovalue can be used to generate a domain from a real-space field data like the density
mask = domain_isovalue(scf.n, 1e-3)
view_atoms(atoms, atoms.r[mask])

# The same can be done for orbitals
from eminus.orbitals import KSO
psi = KSO(scf)
# mask = domain_isovalue(psi[0, :, 0], 1e-2)
# view_atoms(atoms, atoms.r[mask])

In [7]:
# Compare to the density volume plot
view_atoms(scf, plot_n=True, percent=95)

In [8]:
# Truncated densities can be used to calculate, e.g., SIC energies
# Calculate the single-electron densities from Kohn-Sham orbitals first
ni = get_n_single(atoms, atoms.J(psi))

In [9]:
# Calculate the SIC energy for untruncated densities
start = time.perf_counter()
esic = get_Esic(scf, scf.W, ni)
end = time.perf_counter()
print(f'Esic(untruncated) = {esic:.9f} Eh\nTime(untruncated) =  {end - start:.6f} s')

# Calculate the SIC energy for truncated densities
# One can notice a small energy deviation, but a faster calculation time
mask = domain_isovalue(ni, 1e-4)
ni_trunc = truncate(ni, mask)
start = time.perf_counter()
esic_trunc = get_Esic(scf, scf.W, ni_trunc)
end = time.perf_counter()
print(f'Esic( truncated ) = {esic_trunc:.9f} Eh\nTime( truncated ) =  {end - start:.6f} s')

Esic(untruncated) = -0.202930167 Eh
Time(untruncated) =  0.032353 s
Esic( truncated ) = -0.204070554 Eh
Time( truncated ) =  0.006719 s


In [ ]:
# The truncated SIC energy will converge for smaller isovalues to the untruncated value
mask = domain_isovalue(ni, 0)
ni_trunc = truncate(ni, mask)
esic_trunc = get_Esic(scf, scf.W, ni_trunc)
print(esic == esic_trunc)